# Data Drift Analyse

- Consigne: 

L’utilisation de la librairie evidently pour détecter dans le futur du Data Drift en production. Pour cela vous prendrez comme hypothèse que le dataset “application_train” représente les datas pour la modélisation et le dataset “application_test” représente les datas de nouveaux clients une fois le modèle en production. 

L’analyse à l’aide d’evidently vous permettra de détecter éventuellement du Data Drift sur les principales features, entre les datas d’entraînement et les datas de production, au travers du tableau HTML d’analyse que vous aurez réalisé.

In [1]:
try:
    import evidently
except:
    !pip install git+https://github.com/evidentlyai/evidently.git

In [ ]:
import pandas as pd
import numpy as np

In [23]:
import pandas as pd

from sklearn import datasets

from evidently.test_suite import TestSuite
from evidently.test_preset import DataStabilityTestPreset

from evidently.report import Report
from evidently.metric_preset import DataDriftPreset, ClassificationPreset

#iris_data = datasets.load_iris(as_frame='auto')
#iris_frame = iris_data.frame

# Analyse Data Drift

In [35]:
import pickle
from pathlib import Path
from evidently import ColumnMapping
from evidently.report import Report
from evidently.metric_preset import DataDriftPreset
import pandas as pd
import os
from io import StringIO, BytesIO
PROJECT_ROOT = Path(os.path.dirname(os.path.abspath("")))
PROJECT_ROOT = str(PROJECT_ROOT)
PROJECT_ROOT

'/Users/kone/Desktop/Oc_Formation/Projets/Projet7/openclassrooms_projects7'

In [36]:
# Chargement d'un model depuis un fichier pickle depuis Azure
sap_blob_url = "https://dashboardd.blob.core.windows.net/dashboarddata/model_and_data/model.pkl"
r = requests.get(sap_blob_url)
model = pickle.load(BytesIO(r.content))

In [37]:
model

Pipeline(steps=[('smote', SMOTE(k_neighbors=17, random_state=1001)),
                ('model',
                 RandomForestClassifier(max_depth=20, min_samples_leaf=10,
                                        min_samples_split=6,
                                        n_estimators=882))])

## Raw data application_train and Test

In [4]:
application_train = pd.read_csv(
    PROJECT_ROOT + '/data/tables/application_train.csv', index_col=[0]
    )
application_test = pd.read_csv(PROJECT_ROOT + '/data/tables/application_test.csv', index_col=[0])
#data/tables/application_test.csv

In [5]:
application_train.head()

TARGET NAME_CONTRACT_TYPE CODE_GENDER FLAG_OWN_CAR  \
SK_ID_CURR                                                       
100002           1         Cash loans           M            N   
100003           0         Cash loans           F            N   
100004           0    Revolving loans           M            Y   
100006           0         Cash loans           F            N   
100007           0         Cash loans           M            N   

           FLAG_OWN_REALTY  CNT_CHILDREN  AMT_INCOME_TOTAL  AMT_CREDIT  \
SK_ID_CURR                                                               
100002                   Y             0          202500.0    406597.5   
100003                   N             0          270000.0   1293502.5   
100004                   Y             0           67500.0    135000.0   
100006                   Y             0          135000.0    312682.5   
100007                   Y             0          121500.0    513000.0   

            AMT_ANNUITY  AMT_GOODS_PRICE  ... FLAG_DOCUMENT_18  \
SK_ID_CURR                                ...                    
100002          24700.5         351000.0  ...                0   
100003          35698.5        1129500.0  ...                0   
100004           6750.0         135000.0  ...                0   
100006          29686.5         297000.0  ...                0   
100007          21865.5         513000.0  ...                0   

           FLAG_DOCUMENT_19 FLAG_DOCUMENT_20 FLAG_DOCUMENT_21  \
SK_ID_CURR                                                      
100002                    0                0                0   
100003                    0                0                0   
100004                    0                0                0   
100006                    0                0                0   
100007                    0                0                0   

           AMT_REQ_CREDIT_BUREAU_HOUR  AMT_REQ_CREDIT_BUREAU_DAY  \
SK_ID_CURR                                                         
100002                            0.0                        0.0   
100003                            0.0                        0.0   
100004                            0.0                        0.0   
100006                            NaN                        NaN   
100007                            0.0                        0.0   

            AMT_REQ_CREDIT_BUREAU_WEEK  AMT_REQ_CREDIT_BUREAU_MON  \
SK_ID_CURR                                                          
100002                             0.0                        0.0   
100003                             0.0                        0.0   
100004                             0.0                        0.0   
100006                             NaN                        NaN   
100007                             0.0                        0.0   

            AMT_REQ_CREDIT_BUREAU_QRT  AMT_REQ_CREDIT_BUREAU_YEAR  
SK_ID_CURR                                                         
100002                            0.0                         1.0  
100003                            0.0                         0.0  
100004                            0.0                         0.0  
100006                            NaN                         NaN  
100007                            0.0                         0.0  

[5 rows x 121 columns]

In [6]:
application_test.head()

NAME_CONTRACT_TYPE CODE_GENDER FLAG_OWN_CAR FLAG_OWN_REALTY  \
SK_ID_CURR                                                               
100001             Cash loans           F            N               Y   
100005             Cash loans           M            N               Y   
100013             Cash loans           M            Y               Y   
100028             Cash loans           F            N               Y   
100038             Cash loans           M            Y               N   

            CNT_CHILDREN  AMT_INCOME_TOTAL  AMT_CREDIT  AMT_ANNUITY  \
SK_ID_CURR                                                            
100001                 0          135000.0    568800.0      20560.5   
100005                 0           99000.0    222768.0      17370.0   
100013                 0          202500.0    663264.0      69777.0   
100028                 2          315000.0   1575000.0      49018.5   
100038                 1          180000.0    625500.0      32067.0   

            AMT_GOODS_PRICE NAME_TYPE_SUITE  ... FLAG_DOCUMENT_18  \
SK_ID_CURR                                   ...                    
100001             450000.0   Unaccompanied  ...                0   
100005             180000.0   Unaccompanied  ...                0   
100013             630000.0             NaN  ...                0   
100028            1575000.0   Unaccompanied  ...                0   
100038             625500.0   Unaccompanied  ...                0   

           FLAG_DOCUMENT_19 FLAG_DOCUMENT_20 FLAG_DOCUMENT_21  \
SK_ID_CURR                                                      
100001                    0                0                0   
100005                    0                0                0   
100013                    0                0                0   
100028                    0                0                0   
100038                    0                0                0   

            AMT_REQ_CREDIT_BUREAU_HOUR  AMT_REQ_CREDIT_BUREAU_DAY  \
SK_ID_CURR                                                          
100001                             0.0                        0.0   
100005                             0.0                        0.0   
100013                             0.0                        0.0   
100028                             0.0                        0.0   
100038                             NaN                        NaN   

            AMT_REQ_CREDIT_BUREAU_WEEK  AMT_REQ_CREDIT_BUREAU_MON  \
SK_ID_CURR                                                          
100001                             0.0                        0.0   
100005                             0.0                        0.0   
100013                             0.0                        0.0   
100028                             0.0                        0.0   
100038                             NaN                        NaN   

            AMT_REQ_CREDIT_BUREAU_QRT  AMT_REQ_CREDIT_BUREAU_YEAR  
SK_ID_CURR                                                         
100001                            0.0                         0.0  
100005                            0.0                         3.0  
100013                            1.0                         4.0  
100028                            0.0                         3.0  
100038                            NaN                         NaN  

[5 rows x 120 columns]

In [7]:
application_test.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 48744 entries, 100001 to 456250
Columns: 120 entries, NAME_CONTRACT_TYPE to AMT_REQ_CREDIT_BUREAU_YEAR
dtypes: float64(65), int64(39), object(16)
memory usage: 45.0+ MB


In [8]:
def get_cat_feature(data):
    
    cat_colums = data.select_dtypes(include='object').columns.tolist()
    cols = data.select_dtypes(exclude='object').columns.tolist()
    
    for var in cols:
        values_uniq = data[var].unique()
        if len(values_uniq) == 2:
            if 1 in  values_uniq and 0 in  values_uniq:
                cat_colums.append(var)
    return cat_colums

In [9]:
cat_features = get_cat_feature(application_test)
cat_features

['NAME_CONTRACT_TYPE',
 'CODE_GENDER',
 'FLAG_OWN_CAR',
 'FLAG_OWN_REALTY',
 'NAME_TYPE_SUITE',
 'NAME_INCOME_TYPE',
 'NAME_EDUCATION_TYPE',
 'NAME_FAMILY_STATUS',
 'NAME_HOUSING_TYPE',
 'OCCUPATION_TYPE',
 'WEEKDAY_APPR_PROCESS_START',
 'ORGANIZATION_TYPE',
 'FONDKAPREMONT_MODE',
 'HOUSETYPE_MODE',
 'WALLSMATERIAL_MODE',
 'EMERGENCYSTATE_MODE',
 'FLAG_MOBIL',
 'FLAG_EMP_PHONE',
 'FLAG_WORK_PHONE',
 'FLAG_CONT_MOBILE',
 'FLAG_PHONE',
 'FLAG_EMAIL',
 'REG_REGION_NOT_LIVE_REGION',
 'REG_REGION_NOT_WORK_REGION',
 'LIVE_REGION_NOT_WORK_REGION',
 'REG_CITY_NOT_LIVE_CITY',
 'REG_CITY_NOT_WORK_CITY',
 'LIVE_CITY_NOT_WORK_CITY',
 'FLAG_DOCUMENT_3',
 'FLAG_DOCUMENT_4',
 'FLAG_DOCUMENT_5',
 'FLAG_DOCUMENT_6',
 'FLAG_DOCUMENT_7',
 'FLAG_DOCUMENT_8',
 'FLAG_DOCUMENT_9',
 'FLAG_DOCUMENT_11',
 'FLAG_DOCUMENT_18']

In [10]:
column_mapping = ColumnMapping()
column_mapping.categorical_features = cat_features

In [11]:
#drop TAGET columns
Target = application_train.TARGET
del application_train['TARGET']

In [12]:
application_train.reset_index(drop=True, inplace=True)
application_test.reset_index(drop=True, inplace=True)

In [17]:
data_drift_report = Report(metrics=[
    DataDriftPreset(
        #num_stattest='ks', 
        cat_stattest='psi', 
        #num_stattest_threshold=0.1, 
        cat_stattest_threshold=0.1),
])

data_drift_report.run(
    reference_data=application_train.sample(20000, random_state=42), 
    current_data=application_test.sample(20000, random_state=42),
    column_mapping=column_mapping
)
data_drift_report

## Train Data

In [61]:
import requests
from io import StringIO
import numpy as np

def read_csv_from_azure(relatif_path:str):

    # URL SAP de l'objet blob
    if 'data' in relatif_path:
        sap_blob_url = "https://dashboardd.blob.core.windows.net/dashboarddata/" + relatif_path
    else:
        sap_blob_url = "https://dashboardd.blob.core.windows.net/dashboarddata/model_and_data/" + relatif_path

    # Récupération du fichier csv
    r = requests.get(sap_blob_url)

    # Création du dataframe
    df = pd.read_csv(StringIO(r.text), index_col=[0])
    return df

In [95]:
g_df = read_csv_from_azure('golbal_feature_importance.csv')
g_df.sort_values(by='Importance', inplace=True, ascending=False)
g_df_f = g_df[g_df.Importance >= 0.003]
g_df_f.shape

(80, 2)

In [96]:
features = g_df_f.Feature.tolist()
#features.append("TARGET_PROBA")
features

['NAME_INCOME_TYPE_Working',
 'EXT_SOURCE_2',
 'CODE_GENDER',
 'NAME_EDUCATION_TYPE_Highereducation',
 'NAME_EDUCATION_TYPE_Secondarysecondaryspecial',
 'NAME_FAMILY_STATUS_Married',
 'EXT_SOURCE_3',
 'FLAG_OWN_CAR',
 'YEARS_BEGINEXPLUATATION_AVG',
 'HOUSETYPE_MODE_blockofflats',
 'NAME_INCOME_TYPE_Commercialassociate',
 'FLAG_PHONE',
 'OCCUPATION_TYPE_Laborers',
 'NAME_TYPE_SUITE_Unaccompanied',
 'EXT_SOURCE_1',
 'ORGANIZATION_TYPE_BusinessEntityType3',
 'PREV_NAME_CLIENT_TYPE_New_MEAN',
 'INSTAL_PAYMENT_DIFF_MAX',
 'WALLSMATERIAL_MODE_Stonebrick',
 'FLOORSMAX_AVG',
 'NAME_INCOME_TYPE_Pensioner',
 'WALLSMATERIAL_MODE_Panel',
 'REGION_RATING_CLIENT',
 'DAYS_EMPLOYED',
 'DAYS_EMPLOYED_PERC',
 'INSTAL_PAYMENT_DIFF_MEAN',
 'NAME_FAMILY_STATUS_Singlenotmarried',
 'INSTAL_DPD_MEAN',
 'OWN_CAR_AGE',
 'INSTAL_DPD_SUM',
 'INSTAL_PAYMENT_DIFF_SUM',
 'PREV_NAME_YIELD_GROUP_high_MEAN',
 'WEEKDAY_APPR_PROCESS_START_MONDAY',
 'ENTRANCES_AVG',
 'FONDKAPREMONT_MODE_regoperaccount',
 'INSTAL_AMT_PAYME

In [71]:
X_train = read_csv_from_azure("X_train.csv")
test_df = read_csv_from_azure("test_df.csv")
target = read_csv_from_azure("y_train.csv")

In [72]:
X_train.shape

(23062, 374)

In [73]:
target.shape

(23062, 1)

In [74]:
target.columns

Index(['TARGET'], dtype='object')

In [75]:
test_df.shape

(4874, 374)

In [57]:
test_df = test_df.reset_index(drop=True)
test_df.shape

(4874, 375)

In [59]:
#X_train["TARGET_PROBA"] = model.predict_proba(X_train[X_train.columns.tolist()])[:, 1]
#test_df["TARGET_PROBA"] = model.predict_proba(test_df[test_df.columns.tolist()])[:, 1]

test_target = np.where(test_df["TARGET_PROBA"] >= 0.2, 1, 0)
test_target = list(test_target)
test_target

X_train['target'] = target.values
test_df["target"] = test_target

X_train["TARGET_PROBA"]

test_df["TARGET_PROBA"]

In [76]:
X_train.reset_index(drop=True, inplace=True)
X_train.head()

CODE_GENDER  FLAG_OWN_CAR  FLAG_OWN_REALTY  CNT_CHILDREN  AMT_CREDIT  \
0            1             0                1     -0.575843   -0.543801   
1            0             0                0     -0.575843   -0.646724   
2            1             0                1     -0.575843   -0.872696   
3            1             0                0      0.829823   -0.971121   
4            0             1                0     -0.575843   -0.483415   

   AMT_ANNUITY  REGION_POPULATION_RELATIVE  DAYS_BIRTH  DAYS_EMPLOYED  \
0    -0.702813                   -1.357486   -0.190638      -1.325052   
1    -0.448423                   -0.118961   -1.232673       0.427583   
2    -0.493134                   -0.804409    0.846576       0.533843   
3    -1.125871                    1.093643    0.962510       0.748987   
4    -0.472783                   -0.908242    0.951950       0.452508   

   DAYS_REGISTRATION  ...  CC_NAME_CONTRACT_STATUS_Refused_MIN  \
0          -1.065084  ...                                  0.0   
1           1.181580  ...                                  0.0   
2           0.850920  ...                                  0.0   
3           1.264031  ...                                  0.0   
4           0.010767  ...                                  0.0   

   CC_NAME_CONTRACT_STATUS_Sentproposal_MIN  \
0                                       0.0   
1                                       0.0   
2                                       0.0   
3                                       0.0   
4                                       0.0   

   CC_NAME_CONTRACT_STATUS_Sentproposal_MAX  \
0                                       0.0   
1                                       0.0   
2                                       0.0   
3                                       0.0   
4                                       0.0   

   CC_NAME_CONTRACT_STATUS_Signed_MAX  CC_NAME_CONTRACT_STATUS_Signed_SUM  \
0                                 0.0                            -0.04444   
1                                 0.0                            -0.04444   
2                                 0.0                            -0.04444   
3                                 0.0                            -0.04444   
4                                 0.0                            -0.04444   

   CC_NAME_CONTRACT_STATUS_nan_MIN  CC_NAME_CONTRACT_STATUS_nan_MAX  \
0                              0.0                              0.0   
1                              0.0                              0.0   
2                              0.0                              0.0   
3                              0.0                              0.0   
4                              0.0                              0.0   

   CC_NAME_CONTRACT_STATUS_nan_MEAN  CC_NAME_CONTRACT_STATUS_nan_SUM  \
0                               0.0                              0.0   
1                               0.0                              0.0   
2                               0.0                              0.0   
3                               0.0                              0.0   
4                               0.0                              0.0   

   CC_NAME_CONTRACT_STATUS_nan_VAR  
0                              0.0  
1                              0.0  
2                              0.0  
3                              0.0  
4                              0.0  

[5 rows x 374 columns]

In [87]:
X_train[features]

NAME_INCOME_TYPE_Working  EXT_SOURCE_2  CODE_GENDER  \
0                           1.0     -0.889042            1   
1                           0.0     -0.093738            0   
2                           1.0     -0.774765            1   
3                           1.0      0.356163            1   
4                           1.0     -0.513267            0   
...                         ...           ...          ...   
23057                       1.0      1.352223            0   
23058                       1.0      0.833860            0   
23059                       0.0      1.099991            1   
23060                       1.0     -0.234267            1   
23061                       1.0     -0.142640            1   

       NAME_EDUCATION_TYPE_Highereducation  \
0                                      0.0   
1                                      0.0   
2                                      0.0   
3                                      0.0   
4                                      1.0   
...                                    ...   
23057                                  0.0   
23058                                  0.0   
23059                                  0.0   
23060                                  0.0   
23061                                  0.0   

       NAME_EDUCATION_TYPE_Secondarysecondaryspecial  \
0                                                1.0   
1                                                1.0   
2                                                0.0   
3                                                1.0   
4                                                0.0   
...                                              ...   
23057                                            1.0   
23058                                            1.0   
23059                                            1.0   
23060                                            1.0   
23061                                            1.0   

       NAME_FAMILY_STATUS_Married  EXT_SOURCE_3  FLAG_OWN_CAR  \
0                             0.0      0.008167             0   
1                             0.0      1.574447             0   
2                             0.0     -0.537855             0   
3                             0.0      0.066935             0   
4                             1.0      1.113229             1   
...                           ...           ...           ...   
23057                         1.0     -0.075522             0   
23058                         0.0     -0.904969             1   
23059                         1.0     -1.523894             0   
23060                         1.0      0.152483             0   
23061                         1.0     -1.523894             0   

       YEARS_BEGINEXPLUATATION_AVG  HOUSETYPE_MODE_blockofflats  ...  \
0                        -1.024029                          0.0  ...   
1                        -1.024029                          0.0  ...   
2                        -1.024029                          0.0  ...   
3                         0.971636                          1.0  ...   
4                        -1.024029                          0.0  ...   
...                            ...                          ...  ...   
23057                     0.958794                          1.0  ...   
23058                    -1.024029                          0.0  ...   
23059                     1.010367                          1.0  ...   
23060                    -1.024029                          0.0  ...   
23061                    -1.024029                          0.0  ...   

       POS_NAME_CONTRACT_STATUS_Demand_MEAN  ORGANIZATION_TYPE_University  \
0                                 -0.024454                           0.0   
1                                 -0.024454                           0.0   
2                                 -0.024454                           0.0   
3                                 -0.024454                           0.0   
4    

In [79]:
test_df.reset_index(drop=True, inplace=True)

In [80]:
test_df.head()

CODE_GENDER  FLAG_OWN_CAR  FLAG_OWN_REALTY  CNT_CHILDREN  AMT_CREDIT  \
0            0             1                0      2.235490    0.626974   
1            1             0                0     -0.575843   -0.751747   
2            1             1                1     -0.575843   -0.643970   
3            0             0                0     -0.575843    0.022294   
4            0             0                1      0.829823   -0.372351   

   AMT_ANNUITY  REGION_POPULATION_RELATIVE  DAYS_BIRTH  DAYS_EMPLOYED  \
0     0.630498                    0.858383    1.076838       0.350184   
1    -0.554188                   -0.839262   -0.875456       0.852623   
2     0.585479                    0.281126    0.206754      -1.286571   
3     0.282370                   -1.357486    0.189306      -0.359529   
4    -0.285922                   -0.195929    0.053399      -1.690621   

   DAYS_REGISTRATION  ...  CC_NAME_CONTRACT_STATUS_Refused_MIN  \
0          -0.126842  ...                                  0.0   
1           1.366385  ...                                  0.0   
2          -1.214634  ...                                  0.0   
3           0.830734  ...                                  0.0   
4           1.083206  ...                                  0.0   

   CC_NAME_CONTRACT_STATUS_Sentproposal_MIN  \
0                                       0.0   
1                                       0.0   
2                                       0.0   
3                                       0.0   
4                                       0.0   

   CC_NAME_CONTRACT_STATUS_Sentproposal_MAX  \
0                                       0.0   
1                                       0.0   
2                                       0.0   
3                                       0.0   
4                                       0.0   

   CC_NAME_CONTRACT_STATUS_Signed_MAX  CC_NAME_CONTRACT_STATUS_Signed_SUM  \
0                                 0.0                            -0.04444   
1                                 0.0                            -0.04444   
2                                 0.0                            -0.04444   
3                                 0.0                            -0.04444   
4                                 0.0                            -0.04444   

   CC_NAME_CONTRACT_STATUS_nan_MIN  CC_NAME_CONTRACT_STATUS_nan_MAX  \
0                              0.0                              0.0   
1                              0.0                              0.0   
2                              0.0                              0.0   
3                              0.0                              0.0   
4                              0.0                              0.0   

   CC_NAME_CONTRACT_STATUS_nan_MEAN  CC_NAME_CONTRACT_STATUS_nan_SUM  \
0                               0.0                              0.0   
1                               0.0                              0.0   
2                               0.0                              0.0   
3                               0.0                              0.0   
4                               0.0                              0.0   

   CC_NAME_CONTRACT_STATUS_nan_VAR  
0                              0.0  
1                              0.0  
2                              0.0  
3                              0.0  
4                              0.0  

[5 rows x 374 columns]

In [97]:
data_drift_report = Report(metrics=[
    DataDriftPreset(), 
])

data_drift_report.run(
    current_data=test_df[features].sample(200, random_state=42), 
    reference_data=X_train[features].sample(200, random_state=42), 
    column_mapping=None #X_train.columns.to_list()
)
data_drift_report

In [83]:
data_drift_report.save_html('data_drift_report.html')

In [82]:
data_drift_report.save_json('data_drift_report.json')

In [20]:
data_drift = TestSuite(tests=[
    DataDriftTestPreset(stattest='psi'),
])

data_drift.run(current_data=test_df.sample(200, random_state=42), reference_data=X_train.sample(200, random_state=42))
data_drift